## IMPORTS and UTILS

In [1]:
print("hi")

import os
import pandas as pd
import subprocess
import re
import numpy as np
import json
import csv

from joblib import Parallel, delayed



import matplotlib.pyplot as plt


import os

from robust_evaluation_tools.robust_utils import get_site, get_metric, get_disease, add_nb_patients_and_diseased, get_diseases, get_metrics
from robust_evaluation_tools.robust_harmonization import fit, apply, QC, compare_with_compilation 
from robust_evaluation_tools.synthectic_sites_generations import generate_sites

SYNTHETIC_SITES = "RESULTS/IMPACT_SICK/SYNTHETIC_SITES"

MAINFOLDER = "RESULTS/IMPACT_SICK/RESULTS"

ANALYSISFOLDER = "RESULTS/IMPACT_SICK/ANALYSIS"

all_diseases = get_diseases(True)

metrics = get_metrics()

hi


## HARMONIZATION

In [2]:
def harmonize(f_train,f_test, ref_data_file, metric, harmonizartion_method,  directory, robust, rwp,hc):
    os.makedirs(directory, exist_ok=True)
    
    # Fit the model
    output_model_filename = fit(f_train, ref_data_file, metric, harmonizartion_method, robust, rwp, directory, hc,)
    # Apply the model
    output_filename = apply(f_test, output_model_filename, metric, harmonizartion_method, robust, rwp, directory)
    
    # Perform quality control
    dists, bundle_names = QC(ref_data_file, output_filename, output_model_filename)
    dists_df = pd.DataFrame([dists], columns=bundle_names)
    dists_df['site'] = get_site(f_train)
    dists_df['metric'] = get_metric(f_train)
    dists_df['disease'] = get_disease(f_train)

    mea = compare_with_compilation(pd.read_csv(output_filename))
    mea['site'] = get_site(f_train)
    mea['metric'] = get_metric(f_train)
    mea['disease'] = get_disease(f_train)
    
    return[dists_df, mea]

In [3]:
def analyse_site(f_train,f_test,ref_data_file,metric,harmonizartion_method, directory):
    # 4 harmonization
    harmonization_hc = harmonize(f_train, f_test, ref_data_file, metric, harmonizartion_method, os.path.join(directory, "hc"), "No", False, True)
    harmonization_sick = harmonize(f_train, f_test,ref_data_file, metric, harmonizartion_method, os.path.join(directory, "sick"), "No", False, False)

    distances_combined = pd.concat([harmonization_hc[0], harmonization_sick[0]], ignore_index=True)
    distances_combined['method'] = ['hc', 'no_robust']

    # Combine MEA in a single DataFrame
    mea_combined = pd.concat([harmonization_hc[1], harmonization_sick[1]], ignore_index=True)
    mea_combined['method'] = ['hc', 'no_robust']


    #TODO bundles et analyze outliers
    return distances_combined, mea_combined

In [4]:
def process_sample(disease, sample_size, disease_ratio, i, metric, main_directory, directory_site, harmonizartion_method):
    sizeDir = os.path.join(main_directory, disease, f"{sample_size}_{int(disease_ratio*100)}")
    sizeDir_site = os.path.join(directory_site, disease, f"{sample_size}_{int(disease_ratio*100)}")
    tempDir = os.path.join(sizeDir, f"{i}")
    tempDir_site = os.path.join(sizeDir_site, f"{i}")
    
    os.makedirs(tempDir, exist_ok=True)

    train_file_name = f"train_{sample_size}_{int(disease_ratio*100)}_{i}_{metric}.csv"
    test_file_name = f"test_{sample_size}_{int(disease_ratio*100)}_{i}_{metric}.csv"

    # Load and save the training dataset
    temp_file = os.path.join(tempDir_site, train_file_name)
    train_df = pd.read_csv(temp_file)
    train_df.to_csv(os.path.join(tempDir, train_file_name), index=False)

    # Load and save the test dataset
    test_file = os.path.join(tempDir_site, test_file_name)
    test_df = pd.read_csv(test_file)
    test_df.to_csv(os.path.join(tempDir, test_file_name), index=False)

    # Reference data file
    ref_data_file = os.path.join('DONNES', 'CamCAN', f"CamCAN.{metric}.raw.csv.gz")

    # Analyze the site
    dists_analyze, mea_analyze = analyse_site(temp_file, test_file, ref_data_file, metric, harmonizartion_method, tempDir)

    return dists_analyze, mea_analyze

In [5]:
    
#Analyse Method
def analyse_method(sample_sizes, disease_ratios, num_tests,metrics, harmonizartion_method, main_directory, SYNTHETIC_SITES_VERSION):
    directory_site = os.path.join(SYNTHETIC_SITES, SYNTHETIC_SITES_VERSION)

    # Run in parallel
    results = Parallel(n_jobs=-1)(
        delayed(process_sample)(disease, sample_size, disease_ratio, i, metric, main_directory, directory_site, harmonizartion_method)
        for disease in all_diseases
        for sample_size in sample_sizes
        for disease_ratio in disease_ratios
        for i in range(num_tests)
        for metric in metrics
    )

    print("done")

    # Unpack results and concatenate them
    dists_compilation = pd.concat([res[0] for res in results if res[0] is not None], ignore_index=True)
    mea_compilation = pd.concat([res[1] for res in results if res[1] is not None], ignore_index=True)

    # Save results
    dists_compilation.to_csv(os.path.join(main_directory, "dists_compilation.csv"), index=False)
    mea_compilation.to_csv(os.path.join(main_directory, "mea_compilation.csv"), index=False)

In [6]:
def generate_sites_for_disease(disease, raw_directory, SYNTHETIC_SITES, SYNTHETIC_SITES_VERSION, sample_sizes, disease_ratios, num_tests):
    # Load data for the disease
    data_path = os.path.join(raw_directory, f'{disease}_combination_all_metrics_CamCAN.csv.gz')

    # Define site directory
    directory_site = os.path.join(SYNTHETIC_SITES, SYNTHETIC_SITES_VERSION, disease)

    # Generate synthetic sites
    generate_sites(sample_sizes, disease_ratios, num_tests, directory_site, data_path, disease=None)


## EXECUTOR

In [7]:
harmonizartion_method= "classic"

SYNTHETIC_SITES_VERSION = "v1"
# raw_directory = os.path.join('DONNES', 'COMPILATIONS')
raw_directory = os.path.join('DONNES', 'COMPILATIONS_AUG_3')

sample_sizes = [40,100]  # Différentes tailles d'échantillon
disease_ratios = [0, 0.1, 0.3, 0.5]  # Différents pourcentages de malades
#sample_sizes = [150, 300]  # Différentes tailles d'échantillon
#disease_ratios = [0.3]  # Différents pourcentages de malades
num_tests = 10  # Nombre de tests à effectuer pour chaque combinaison

Parallel(n_jobs=-1)(
    delayed(generate_sites_for_disease)(disease, raw_directory, SYNTHETIC_SITES, SYNTHETIC_SITES_VERSION, sample_sizes, disease_ratios, num_tests)
    for disease in all_diseases
)

print("process starts")



/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/synthectic_sites_generations.py:161: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(data_path)
/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/synthectic_sites_generations.py:161: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(data_path)
/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/synthectic_sites_generations.py:161: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(data_path)


process starts


In [8]:
analyse_method(sample_sizes, disease_ratios, num_tests, metrics,harmonizartion_method, MAINFOLDER, SYNTHETIC_SITES_VERSION)

      Mean Bhattacharrya distance: 0.003325 (min: 0.000028, max: 0.012030)


/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/robust_harmonization.py:243: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  compilation_df = pd.read_csv(compilation_file, compression='gzip')


      Mean Bhattacharrya distance: 0.001086 (min: 0.000009, max: 0.002836)
      Mean Bhattacharrya distance: 0.001998 (min: 0.000105, max: 0.008269)
      Mean Bhattacharrya distance: 0.001065 (min: 0.000038, max: 0.003639)
      Mean Bhattacharrya distance: 0.004796 (min: 0.000060, max: 0.018275)
      Mean Bhattacharrya distance: 0.003757 (min: 0.000184, max: 0.013561)
      Mean Bhattacharrya distance: 0.011506 (min: 0.001316, max: 0.022792)
      Mean Bhattacharrya distance: 0.001227 (min: 0.000011, max: 0.007324)
      Mean Bhattacharrya distance: 0.023876 (min: 0.004143, max: 0.045662)
      Mean Bhattacharrya distance: 0.003638 (min: 0.000008, max: 0.019607)
      Mean Bhattacharrya distance: 0.001632 (min: 0.000045, max: 0.006786)
      Mean Bhattacharrya distance: 0.002196 (min: 0.000024, max: 0.006692)
      Mean Bhattacharrya distance: 0.001236 (min: 0.000012, max: 0.010174)
      Mean Bhattacharrya distance: 0.003346 (min: 0.000189, max: 0.012032)
      Mean Bhattacharrya 

/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/robust_harmonization.py:243: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  compilation_df = pd.read_csv(compilation_file, compression='gzip')
/home/local/USHERBROOKE/davy3001/Documents/COMBAT/Jodoin/Combat_robust/robust_evaluation_tools/robust_harmonization.py:243: DtypeWarning: Columns (9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  compilation_df = pd.read_csv(compilation_file, compression='gzip')


      Mean Bhattacharrya distance: 0.004222 (min: 0.000387, max: 0.012979)


...

      Mean Bhattacharrya distance: 0.023130 (min: 0.013854, max: 0.050314)
      Mean Bhattacharrya distance: 0.035560 (min: 0.022322, max: 0.062188)


      Mean Bhattacharrya distance: 0.024368 (min: 0.014677, max: 0.036479)
      Mean Bhattacharrya distance: 0.010306 (min: 0.000023, max: 0.033269)
      Mean Bhattacharrya distance: 0.013373 (min: 0.000230, max: 0.036960)
      Mean Bhattacharrya distance: 0.024574 (min: 0.012697, max: 0.048663)
      Mean Bhattacharrya distance: 0.028784 (min: 0.016304, max: 0.050831)


      Mean Bhattacharrya distance: 0.008449 (min: 0.000026, max: 0.027886)
      Mean Bhattacharrya distance: 0.030645 (min: 0.002993, max: 0.071458)
      Mean Bhattacharrya distance: 0.018214 (min: 0.000363, max: 0.054523)
      Mean Bhattacharrya distance: 0.009705 (min: 0.000131, max: 0.032281)


      Mean Bhattacharrya distance: 0.005663 (min: 0.000033, max: 0.026151)


      Mean Bhattacharrya distance: 0.038644 (min: 0.020113, max: 0.064430)
      Mean Bhattacharrya distance: 0.020374 (min: 0.006977, max: 0.046398)
      Mean Bhattacharrya distance: 0.039333 (min: 0.012586, max: 0.066946)
      Mean Bhattacharrya distance: 0.027513 (min: 0.008128, max: 0.055805)
      Mean Bhattacharrya distance: 0.018149 (min: 0.006223, max: 0.043201)
      Mean Bhattacharrya distance: 0.030343 (min: 0.014560, max: 0.068821)
      Mean Bhattacharrya distance: 0.041410 (min: 0.008390, max: 0.074791)
      Mean Bhattacharrya distance: 0.034570 (min: 0.007011, max: 0.066513)
      Mean Bhattacharrya distance: 0.026415 (min: 0.012355, max: 0.047729)
      Mean Bhattacharrya distance: 0.034309 (min: 0.015216, max: 0.064726)
done


## ANALYSYS

In [9]:
# # Moyenne par site
# # Nothing really interesting so far

# directory = ANALYSISFOLDER
# os.makedirs(directory, exist_ok=True)

# dists_compilation['site'] = dists_compilation['site'].str.rsplit('_', n=1).str[0]
# metrics_compilation['site'] = metrics_compilation['site'].str.rsplit('_', n=1).str[0]

# # Display the means by site
# dists_means_by_site = dists_compilation.groupby(['site','method']).mean().reset_index()
# metrics_means_by_site = metrics_compilation.groupby(['site', 'metric']).mean().reset_index()

# metrics_means_by_site.to_csv(os.path.join(directory, "metrics_compilation_mean.csv"), index=False)
# dists_means_by_site.to_csv(os.path.join(directory, "dists_compilation_mean.csv"), index=False)
# print("FINI")

In [10]:

# # Exemple d'utilisation
# precision_df = calculate_precision_by_bundle(pd.read_csv(os.path.join(MAINFOLDER, robust_method, "metrics_compilation.csv")))
# precision_df = precision_df.sort_values(by='precision', ascending=False)
# precision_df.to_csv(os.path.join(directory, "metrics_per_bundle.csv"), index=False)

In [11]:
# precision_df = precision_df.sort_values(by='precision', ascending=False)
# precision_df.head()

In [12]:
# precision_df = precision_df.sort_values(by='f1_score', ascending=False)
# precision_df.head()

In [13]:
# Function to generate box plots for one combination of (disease, sample_size, metric)
def plot_bundle_battacharyya(df, sample_size, disease, metric, directory):
    """
    Creates box plots for each bundle in the DataFrame.
    
    Parameters:
    df (pd.DataFrame): The DataFrame containing the data.
    sample_size (int): The sample size to filter.
    disease (str): The disease type.
    metric (str): The metric used.
    directory (str): The base directory for saving plots.
    """
    directory = os.path.join(directory, "DISTANCES_PLOTS", disease, metric, str(sample_size))
    os.makedirs(directory, exist_ok=True)
    
    df_filtered = df[
        (df['num_patients'] == sample_size) &
        (df['disease'] == disease) &
        (df['metric'] == metric)
    ]

    for bundle_column in df_filtered.columns:
        if bundle_column in ['site', 'method', 'num_patients', 'disease_ratio', 'num_diseased', 'metric', 'disease']:
            continue  # Skip non-numeric columns

        bundle_df = df_filtered[[bundle_column, 'site', 'method', 'num_patients', 'disease_ratio', 'num_diseased']].copy()
        methods = ["hc", "no_robust"]
        colors = ['green', 'red']

        plt.figure(figsize=(10, 5))
        width = 0.2  # Width of the bars
        x = np.arange(len(bundle_df['disease_ratio'].unique()))  # Label locations
        fig, ax = plt.subplots(figsize=(10, 5))

        for i, (method, color) in enumerate(zip(methods, colors)):
            method_df = bundle_df[bundle_df['method'] == method]
            data = [method_df[method_df['disease_ratio'] == patients][bundle_column].values 
                    for patients in bundle_df['disease_ratio'].unique()]
            
            # Ensure there is data for each disease_ratio
            if any(len(d) > 0 for d in data):
                positions = x + i * width  # Shift positions for each method
                ax.boxplot(data, positions=positions, widths=0.15, patch_artist=True, 
                        boxprops=dict(facecolor=color, color=color),
                        medianprops=dict(color='black'))
                
        ax.set_xlabel('% de patients malades')
        ax.set_ylabel('Distance de Battacharyya')
        ax.set_title(f"Distance de Battacharyya de l'harmonization selon le pourcentage de patients malades \n Maladie:{disease} Metric:{metric} Bundle:{bundle_column} Nb patient total: {sample_size}")
        ax.set_xticks(x + width * (len(methods) - 1) / 2)
        ax.set_xticklabels(bundle_df['disease_ratio'].unique())
        ax.legend(handles=[plt.Line2D([0], [0], color=color, lw=2, label=f'Method: {method}') for method, color in zip(methods, colors)])
        plt.savefig(os.path.join(directory, f'{bundle_column}_boxplot.png'))
        plt.close()

# Load dataset
distances_df = pd.read_csv(os.path.join(MAINFOLDER, "dists_compilation.csv"))
add_nb_patients_and_diseased(distances_df)

# Generate all task combinations
tasks = [
    (distances_df, sample_size, disease, metric, ANALYSISFOLDER)
    for disease in all_diseases
    for sample_size in sample_sizes
    for metric in metrics
]

# Run all tasks in parallel
Parallel(n_jobs=-1)(
    delayed(plot_bundle_battacharyya)(*task) for task in tasks
)

/tmp/ipykernel_1739515/116108902.py:33: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
/tmp/ipykernel_1739515/116108902.py:33: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
/tmp/ipykernel_1739515/116108902.py:33: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_o

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [14]:
# Function to generate MAE box plots for a given (disease, sample_size, metric)
def plot_mea(df, sample_size, disease, metric, directory):
    """
    Creates MAE box plots for each bundle in the DataFrame.

    Parameters:
    df (pd.DataFrame): The DataFrame containing the data.
    sample_size (int): The sample size to filter.
    disease (str): The disease type.
    metric (str): The metric used.
    directory (str): The base directory for saving plots.
    """
    directory = os.path.join(directory, "MAE_PLOTS", disease, metric, str(sample_size))
    os.makedirs(directory, exist_ok=True)
    
    df_filtered = df[
        (df['num_patients'] == sample_size) &
        (df['disease'] == disease) &
        (df['metric'] == metric)
    ]

    for bundle_column in df_filtered.columns:
        if bundle_column in ['site', 'method', 'num_patients', 'disease_ratio', 'num_diseased', 'metric', 'disease']:
            continue  # Skip non-numeric columns

        bundle_df = df_filtered[[bundle_column, 'site', 'method', 'num_patients', 'disease_ratio', 'num_diseased']].copy()
        methods = ["hc", "no_robust"]
        colors = ['green', 'red']

        plt.figure(figsize=(10, 5))
        width = 0.2  # Width of the bars
        x = np.arange(len(bundle_df['disease_ratio'].unique()))  # Label locations
        fig, ax = plt.subplots(figsize=(10, 5))

        for i, (method, color) in enumerate(zip(methods, colors)):
            method_df = bundle_df[bundle_df['method'] == method]
            data = [method_df[method_df['disease_ratio'] == patients][bundle_column].values 
                    for patients in bundle_df['disease_ratio'].unique()]
            
            # Ensure there is data for each disease_ratio
            if any(len(d) > 0 for d in data):
                positions = x + i * width  # Shift positions for each method
                ax.boxplot(data, positions=positions, widths=0.15, patch_artist=True, 
                        boxprops=dict(facecolor=color, color=color),
                        medianprops=dict(color='black'))
                
        ax.set_xlabel('Prct de patients malades')
        ax.set_ylabel('MAE')
        ax.set_title(f"MAE de l'harmonization selon le pourcentage de patients malades \n Maladie:{disease} Metric:{metric} Bundle:{bundle_column} Nb patient total: {sample_size}")
        ax.set_xticks(x + width * (len(methods) - 1) / 2)
        ax.set_xticklabels(bundle_df['disease_ratio'].unique())
        ax.legend(handles=[plt.Line2D([0], [0], color=color, lw=2, label=f'Method: {method}') for method, color in zip(methods, colors)])
        plt.savefig(os.path.join(directory, f'{bundle_column}_boxplot.png'))
        plt.close()

# Load dataset
mea_df = pd.read_csv(os.path.join(MAINFOLDER, "mea_compilation.csv"))
add_nb_patients_and_diseased(mea_df)

# Generate all task combinations
tasks = [
    (mea_df, sample_size, disease, metric, ANALYSISFOLDER)
    for disease in all_diseases
    for sample_size in sample_sizes
    for metric in metrics
]

# Run all tasks in parallel
Parallel(n_jobs=-1)(
    delayed(plot_mea)(*task) for task in tasks
)

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

## TESTS

In [15]:
# # # TEST ADD BIAIS
# # Split the data into training and testing sets
# directory = os.path.join(MAINFOLDER, "testBiais")
# os.makedirs(directory, exist_ok=True)
# train_df, test_df = split_train_test(CAMCAN, test_size=0.2, random_state=42)

# # Generate biased data
# # Save the original non-biased data to temporary files
# temp_train_file_original = os.path.join(directory, "temp_train_original.csv")
# temp_test_file_original = os.path.join(directory, "temp_test_original.csv")
# train_df.to_csv(temp_train_file_original, index=False)
# test_df.to_csv(temp_test_file_original, index=False)

# # Generate biased data
# sampled_df_biaied, test_df_biaised, gammas,deltas, ruffles= generate_biaised_data(train_df, test_df)

# # Save the biased data to temporary files
# temp_train_file = os.path.join(directory, "temp_train_biased.csv")
# temp_test_file = os.path.join(directory, "temp_test_biased.csv")
# sampled_df_biaied.to_csv(temp_train_file, index=False)
# test_df_biaised.to_csv(temp_test_file, index=False)

# # Run the combat_visualize_data script
# outname_train = os.path.join("visualize_train")
# cmd = (
#     "scripts/combat_visualize_data.py"
#     + " "
#     + temp_train_file_original
#     + " "
#     + temp_train_file
#     + " --out_dir "
#     + directory
#     + " --outname "
#     + outname_train
#     + " -f"
#     + " --bundles all"
# )
# subprocess.call(cmd, shell=True)

# # Display gammas and deltas along with their mean and standard deviation
# print("Gammas:", gammas)
# print("Deltas:", deltas)
# gammas = list(gammas.values())
# deltas = list(deltas.values())
# print("\nGamma Statistics:")
# print(f"Mean: {np.mean(gammas)}, Std: {np.std(gammas)}")

# print("\nDelta Statistics:")
# print(f"Mean: {np.mean(deltas)}, Std: {np.std(deltas)}")
# print("Ruffles:", ruffles)


In [16]:
# # TEST Powerpoint generation
# d  = os.path.join(MAINFOLDER, robust_method, "adni_100_Philips_3T")
# create_presentation(d)

In [17]:
# # TEST the sample_patients function with compilation data data
# sampled_df = sample_patients(COMPILATION, num_patients=100, disease_ratio=0.5)
# print(sampled_df)


In [18]:
# load_metrics("ROBUST/IQR/50_30/0/", "50_patients_30_percent_0")

In [19]:
# # Load the dists_compilation and metrics_compilation CSV files
# dists_compilation_path = os.path.join(directory, "dists_compilation.csv")
# metrics_compilation_path = os.path.join(directory, "metrics_compilation.csv")

# dists_compilation = pd.read_csv(dists_compilation_path)
# metrics_compilation = pd.read_csv(metrics_compilation_path)

# # Change the site column
# dists_compilation['site'] = dists_compilation['site'].str.rsplit('_', n=1).str[0]
# metrics_compilation['site'] = metrics_compilation['site'].str.rsplit('_', n=1).str[0]

# # Display the means by site
# dists_means_by_site = dists_compilation.groupby(['site','comparaison']).mean()
# metrics_means_by_site = metrics_compilation.groupby('site').mean()

# print(dists_means_by_site)
# print(metrics_means_by_site)

In [20]:
# # FIX METRICS COMPILATION
# directory = os.path.join(MAINFOLDER, robust_method)
# df = pd.read_csv(os.path.join(directory, "metrics_compilation.csv"))

# # Group by the site
# grouped = df.groupby('site')

# # Process each site
# cleaned_dfs = []
# for site, group in grouped:
#     # Reset index for easier manipulation
#     group = group.reset_index(drop=True)
    
#     # # The first row is the "bundle row" (new column names)
#     # new_columns = group.iloc[0].values  # Extract column names from the first row
#     # new_columns[-1] = 'site'
#     # group = group.iloc[1:]  # Remove the first row
    
#     # # Assign new column names
#     # group.columns = new_columns
    
#     # # Sort the columns alphabetically (excluding 'site')
#     # sorted = group.sort_index(axis=1)
#     # Add a new column 'nomm' with the value indicating the metric for each row
#     metrics = ['tp', 'fp', 'tn', 'fn', 'precision', 'recall', 'taux_faux_positifs', 'f1_score']
#     group['metric'] = metrics
    
#     # # Append the cleaned DataFrame for this site
#     cleaned_dfs.append(group)

# # Concatenate all cleaned DataFrames
# final_df = pd.concat(cleaned_dfs, ignore_index=True)

# # Save or display the result
# final_df.to_csv(os.path.join(directory, "metrics_compilation.csv"), index=False)


In [21]:
# REAL SITES
# directory = os.path.join(MAINFOLDER, robust_method)
# raw_directory = os.path.join(RAWFOLDER, site_group)
# for filename in sorted(os.listdir(raw_directory)):
#     f = os.path.join(raw_directory, filename)
#     # checking if it is a file
#     if os.path.isfile(f):
#         analyse_site(f, robust_method, directory)
        


In [22]:
# ADD METRIC AND DIEASE COLUMNS
# dists_compilation = pd.read_csv(os.path.join(MAINFOLDER, "dists_compilation.csv"))
# mea_compilation = pd.read_csv(os.path.join(MAINFOLDER, "mea_compilation.csv"))
# # List of metrics and diseases
# metrics = ['ad', 'adt', 'afd', 'fa', 'fat', 'fw', 'md', 'mdt', 'rd', 'rdt']
# diseases = ["AD", "ADHD", "BIP", "MCI", "SCHZ", "TBI"]
# # Repeat each metric 2 times and then switch to the next metric
# metrics_repeated = [metric for metric in metrics for _ in range(2)]

# # Repeat the entire metrics list twice for each disease
# metrics_final = metrics_repeated * 8 * len(diseases)

# # Repeat each disease for the length of the metrics list repeated twice
# diseases_final = [disease for disease in diseases for _ in range(len(metrics_repeated) * 8)]

# # Add the new columns to the DataFrame
# dists_compilation['metric'] = metrics_final[:len(dists_compilation)]
# dists_compilation['disease'] = diseases_final[:len(dists_compilation)]

# mea_compilation['metric'] = metrics_final[:len(mea_compilation)]
# mea_compilation['disease'] = diseases_final[:len(mea_compilation)]